A *degree n pillowcase-tiled surface* is represented by a tuple of four elements $(a,b,c,d) \in \text{Sym}(n)^4$
such that $abcd = 1$. A PTS is *1-cylinder* if every element of its braid group orbit has the property that $ab$ is an $n$-cycle. Our goal is to find non-cyclic 1-cylinder PTS, in other words, tuples such that 
* for every $g \in B_4$, if $g\cdot(a,b,c,d) = (a',b',c',d')$ then $a'b'$ is an $n$-cycle, and 
* $\langle a,b,c,d\rangle$ is a non-cyclic subgroup of $\text{Sym}(n)$.  

We're particularly interested if there are examples where the permutations $a,b,c,d$ do not include the identity permutation.

We use the class `Constellation` from the `sage::combinat` library. A *constellation* is a tuple of permutations in $\text{Sym(n)}$ whose product is the identity. The *length* of a constellation is the number of elements in the tuple,
and the *degree* is the $n$ of the symmetric group the permutations come from.
The `constellation` library by default only returns connected constellations, i.e. 
constellations whose permutations have a connected orbit when acting on 
$\{1,\dots,n\}$. In order to be a 1-cylinder surface, a PTS must be represented by a connected 
constellation, so this is ok.

In [15]:
from sage.all import SymmetricGroup
from sage.combinat import constellation
from itertools import islice

n = 6
Sn = SymmetricGroup(n)
all_pts = Constellations(4,n) # only returns connected constellations

In [ ]:
# n = 6 new method 143m finds 361351559
# computed:
# [0, 361351559]
start = 361351559
current = 361351559
# TODO: need to create own batch/indexing for this

horizontal_one_cyl_strings = []
for i,pts in enumerate(islice(all_pts, 361351559, None)):
    print(i)
    current = i
    if (pts.g(0)*pts.g(1)).cycle_type() == [n]:
        horizontal_one_cyl_strings.append(f'{pts.g(0)} {pts.g(1)} {pts.g(2)} {pts.g(3)}')
print(f'Total number of degree {n} PTS: {len(all_pts)}')
print(f'Total number of degree {n} PTS with a horizontal cyl: {len(horizontal_one_cyl_strings)}')

KeyboardInterrupt: 

In [17]:
print(current)


361351559


In [50]:
print(len(horizontal_one_cyl_strings))
print(current)

62208000
361351559


In [ ]:
import pickle

with open(f'horizontal_one_cyl_{n}_found_{len(horizontal_one_cyl_strings)}_index_0_to_{current}.pkl', 'wb') as f:
    pickle.dump(horizontal_one_cyl_strings, f)

In [1]:
import pickle

with open('horizontal_one_cyl_6_found_62208000_index_0_to_361351559.pkl', 'rb') as f:
    horizontal_one_cyl_strings_opened = pickle.load(f)

print(len(horizontal_one_cyl_strings_opened))

62208000


In [2]:
class PTS:
    # n is an integer > 1, constellation is an instance of the Constellation 
    # class on Sym(n)
    def __init__(self, n, constellation):
        self.n = n
        self.constellation = constellation
        self.orbit = None

    def __eq__(self, other):
        return (self.constellation == other.constellation)
    
    def __neq__(self, other):
        return (self.constellation != other.constellation)

    def __hash__(self):
        return self.constellation.__hash__()

    def g(self,i):
        return self.constellation.g(i)
    
    def braid_group_orbit(self):
        orbit = set()
        waiting = [self]

        while waiting:
            
            c = waiting.pop()
            orbit.add(c)
            for i in range(3): # Constellation implements braid of 1st element and 4th element of tuple, which we want to skip, so only index with 0,1,2 here. TODO: ask Paul if this is correct
                cc = c.braid(i) # TODO: is this an error in the original library?
                if cc not in orbit:
                    # print(f'not in orbit')
                    waiting.append(cc)
        return orbit
    
    def iso_class_braid_group_orbit(self):
        orbit = []
        for t in self.constellation.braid_group_orbit().vertices():
            orbit.append(PTS(self.n, t))
        
        return orbit
    
    def braid(self, i):
        return PTS(self.n, self.constellation.braid_group_action(i))

    def is_cyclic(self):
        G = SymmetricGroup(self.n).subgroup([self.g(0), self.g(1), self.g(2), self.g(3)])
        return G.is_cyclic()
    
    def is_normal(self):
        G = SymmetricGroup(self.n).subgroup([self.g(0), self.g(1), self.g(2), self.g(3)])
        return G.is_normal() 
    
    # check if there is one cylinder in the horizontal direction
    def check_horizontal_direction(self):
        if (self.g(0)*self.g(1)).cycle_type() == [self.n]:
            return True 
        else:
            return False
    
    def is_one_cyl_surface(self):
        if self.orbit == None:
            self.braid_group_orbit()

        for t in self.orbit: # t not nec = pts, but will be isom. constellations
            if not PTS(self.n, t).check_horizontal_direction():
                return False
        return True
    
    def contains_identity(self):
        for i in range(0,4):
            if self.g(i).cycle_type() == ([1]*self.n):
                return True 
        return False

    def __str__(self):
        return f' ({self.g(0)},  {self.g(1)},  {self.g(2)},  {self.g(3)})'

    def verbose_print(self):
        print('PTS defined by:')
        print(f' a: {self.g(0)}')
        print(f' b: {self.g(1)}')
        print(f' c: {self.g(2)}')
        print(f' d: {self.g(3)}\n')
    
        print(f'cycle type: {self.constellation.profile()}')
        print(f'is cyclic: {self.is_cyclic()}')
        print(f'is normal: {self.is_normal()}')
        print(f'is 1-cylinder: {self.is_one_cyl_surface()}')
        print(f'Braid group orbit:')
        if self.orbit == None:
            self.orbit = self.braid_group_orbit()
        for t in self.orbit:
            print(t)
        print(f'\n')


In [3]:
n=6
orbit_reps = set()
orbit_computed = set()
reps_computed = 0 # for tracking computation progress
computed = 0
checkpoint = 0

total = len(horizontal_one_cyl_strings_opened)
print(f'computed: 0/{total}')
for pts in horizontal_one_cyl_strings_opened:
    p = PTS(n, Constellation(pts.split(' ')))
    if int(computed/1000) > checkpoint:
        checkpoint = int(computed/1000)
        print(f'computed: {computed}/{total}')
    if p in orbit_computed:
        computed +=1
        continue 
    else:
        print('found a new orbit rep, computing orbit')
        orbit = p.braid_group_orbit()
        orbit_set= set(orbit)
        for o in orbit:
            orbit_computed.add(o)
            computed += 1
        
        p.orbit = orbit
        orbit_reps.add(p)
        reps_computed += 1

        print(f'orbit reps found: {reps_computed}')
    
    if len(orbit_computed) >= 10000000:
        break
print(f'{computed}/{total}')

computed: 0/62208000
found a new orbit rep, computing orbit
orbit reps found: 1
found a new orbit rep, computing orbit
orbit reps found: 2
found a new orbit rep, computing orbit
orbit reps found: 3
computed: 17304/62208000
found a new orbit rep, computing orbit
orbit reps found: 4
found a new orbit rep, computing orbit
orbit reps found: 5
computed: 34610/62208000
found a new orbit rep, computing orbit
orbit reps found: 6
computed: 51890/62208000
found a new orbit rep, computing orbit
orbit reps found: 7
computed: 60530/62208000
found a new orbit rep, computing orbit
orbit reps found: 8
computed: 77816/62208000
found a new orbit rep, computing orbit
orbit reps found: 9
computed: 95096/62208000
found a new orbit rep, computing orbit
orbit reps found: 10
computed: 103736/62208000
found a new orbit rep, computing orbit
orbit reps found: 11
computed: 106630/62208000
found a new orbit rep, computing orbit
orbit reps found: 12
computed: 109513/62208000
found a new orbit rep, computing orbit
o

KeyboardInterrupt: 

In [6]:
import pickle
from datetime import datetime
import json

permutation_strings = [] # TODO: just do this in the first place with horizontal_one_cyl_set
for pts in orbit_reps:
    permutation_strings.append(f'{pts.g(0)} {pts.g(1)} {pts.g(2)} {pts.g(3)}')

with open(f'orbit_reps_{n}_first_{len(permutation_strings)}.pkl', 'wb') as f:
    pickle.dump(permutation_strings, f)

In [11]:
print(len(orbit_reps))
for p in orbit_reps:
    print(p.constellation.profile())

one_cyl_orbit_reps = set()

for pts in orbit_reps:
    if pts.is_one_cyl_surface():
        one_cyl_orbit_reps.add(pts)

print(len(one_cyl_orbit_reps))

172
([1, 1, 1, 1, 1, 1], [6], [1, 1, 1, 1, 1, 1], [6])
([1, 1, 1, 1, 1, 1], [6], [5, 1], [2, 2, 2])
([1, 1, 1, 1, 1, 1], [6], [1, 1, 1, 1, 1, 1], [6])
([1, 1, 1, 1, 1, 1], [6], [6], [2, 2, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [6], [2, 2, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [3, 3], [2, 1, 1, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [5, 1], [4, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [6], [3, 3])
([1, 1, 1, 1, 1, 1], [6], [2, 2, 1, 1], [6])
([1, 1, 1, 1, 1, 1], [6], [2, 2, 1, 1], [4, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [2, 2, 2], [2, 2, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [4, 1, 1], [2, 2, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [3, 2, 1], [4, 2])
([1, 1, 1, 1, 1, 1], [6], [4, 2], [3, 2, 1])
([1, 1, 1, 1, 1, 1], [6], [4, 1, 1], [3, 1, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [2, 2, 2], [3, 1, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [3, 3], [6])
([1, 1, 1, 1, 1, 1], [6], [2, 1, 1, 1, 1], [4, 2])
([1, 1, 1, 1, 1, 1], [6], [4, 2], [3, 2, 1])
([1, 1, 1, 1, 1, 1], [6], [6], [2, 2, 1, 1])
([1, 1, 1, 1, 1, 1], [6], [2, 2, 2], [5, 1])
([1, 1, 1

In [22]:
one_cyl_orbit_reps_cycle_types = {}
for pts in one_cyl_orbit_reps:
    key = tuple(sorted(pts.constellation.profile()))
    if not one_cyl_orbit_reps_cycle_types.get(key)==None:
        one_cyl_orbit_reps_cycle_types.get(key).append(pts)
    else:
        one_cyl_orbit_reps_cycle_types.update({key: [pts]})
print(f'Number of cycle types: {len(one_cyl_orbit_reps_cycle_types.keys())}')
for key in one_cyl_orbit_reps_cycle_types.keys():
    print(f'{len(one_cyl_orbit_reps_cycle_types.get(key))} orbit reps of type {key}')

Number of cycle types: 1
3 orbit reps of type ([1, 1, 1, 1, 1, 1, 1], [7], [7], [7])


In [12]:
rep = list(one_cyl_orbit_reps)[3]
rep.verbose_print()

PTS defined by:
 a: ()
 b: (1,5,2,4,6,3,7)
 c: (1,2,6,5,7,4,3)
 d: (1,6,5,4,3,2,7)

cycle type: ([1, 1, 1, 1, 1, 1, 1], [7], [7], [7])
is cyclic: False
is normal: True
is 1-cylinder: True
Braid group orbit:
 ((1,7,5,4,2,6,3),  (),  (1,2,6,5,3,7,4),  (1,5,2,3,7,6,4))
 ((1,7,6,4,5,3,2),  (),  (1,6,3,4,7,5,2),  (1,3,7,6,2,4,5))
 ((),  (1,7,5,2,4,6,3),  (1,2,6,3,7,5,4),  (1,2,3,4,7,6,5))
 ((),  (1,3,7,6,5,2,4),  (1,5,7,2,3,4,6),  (1,7,6,2,3,5,4))
 ((1,6,7,4,2,5,3),  (1,2,7,3,6,4,5),  (1,2,3,6,5,7,4),  ())
 ((),  (1,6,7,4,5,3,2),  (1,5,2,6,3,7,4),  (1,7,5,2,4,6,3))
 ((1,3,4,2,5,6,7),  (),  (1,2,6,7,3,5,4),  (1,3,6,4,2,7,5))
 ((1,3,7,4,5,6,2),  (1,4,6,2,3,5,7),  (),  (1,3,6,7,4,2,5))
 ((),  (1,7,2,5,4,6,3),  (1,4,7,5,6,2,3),  (1,6,2,4,3,7,5))
 ((),  (1,4,3,7,2,5,6),  (1,3,7,5,4,2,6),  (1,5,3,6,7,4,2))
 ((),  (1,4,2,5,6,3,7),  (1,6,4,7,2,3,5),  (1,2,3,4,5,6,7))
 ((1,2,6,7,4,5,3),  (1,7,5,3,2,4,6),  (),  (1,2,5,6,7,3,4))
 ((1,5,6,4,2,3,7),  (),  (1,4,5,3,6,7,2),  (1,4,7,5,6,2,3))
 ((1,7,3,5,2,

In [13]:
for (i,rep) in enumerate(one_cyl_orbit_reps):
    print(f'{i}: {rep.is_cyclic()}, {len(rep.orbit)}')
    if not rep.is_cyclic():
        print(rep)

0: False, 20160
 ((),  (1,5,7,4,6,3,2),  (1,4,3,2,6,5,7),  (1,5,4,2,6,3,7))
1: False, 30240
 ((),  (1,7,3,6,4,2,5),  (1,2,6,7,5,3,4),  (1,6,4,7,3,2,5))
2: False, 60480
 ((),  (1,3,4,5,7,6,2),  (1,4,7,3,6,2,5),  (1,4,2,7,3,5,6))
3: False, 60480
 ((),  (1,5,2,4,6,3,7),  (1,2,6,5,7,4,3),  (1,6,5,4,3,2,7))
4: False, 30240
 ((),  (1,4,6,5,7,2,3),  (1,4,3,6,2,5,7),  (1,5,7,6,2,4,3))
